In [48]:
import streamlit as st
import pandas as pd
import urllib.request
import json
import zipfile
import requests
from urllib.parse import urlencode
import warnings
import geopandas as gpd
import io
import folium
import shapely as sp
import streamlit.components.v1 as components
import branca.colormap as cm
from datetime import datetime
from shapely.ops import unary_union
import os

In [9]:
routes = pd.read_csv("./GTFS B/routes.txt")
shapes = pd.read_csv("./GTFS B/shapes.txt")
shapes1 = shapes[shapes['shape_id'].str.startswith('B10026')] 
shapes2 = shapes[shapes['shape_id'].str.startswith('B20')] 
shapes

shape_id  shape_pt_lat  shape_pt_lon  shape_pt_sequence
0          B10025     40.578199    -73.939761              10001
1          B10025     40.578252    -73.939799              10002
2          B10025     40.578352    -73.939819              10003
3          B10025     40.578329    -73.940025              10004
4          B10025     40.578329    -73.940025              20001
...           ...           ...           ...                ...
103719  SBS821520     40.644112    -73.877609             220015
103720  SBS821520     40.644022    -73.877519             220016
103721  SBS821520     40.643452    -73.877919             220017
103722  SBS821520     40.643061    -73.878185             220018
103723  SBS821520     40.642962    -73.878253             220019

[103724 rows x 4 columns]

In [20]:


warnings.filterwarnings("ignore")
# Add route click interactivity
route_click_js = """
<script>
function highlightRoute(routeId) {
    // Get all polylines on the map
    var allRoutes = document.querySelectorAll('.leaflet-interactive');
    
    allRoutes.forEach(route => {
        if (route.id === routeId) {
            // Highlight the selected route
            route.style.strokeWidth = "6";  // Make the selected route thicker
            route.style.strokeOpacity = "1";  // Full opacity
        } else {
            // Dim all other routes
            route.style.strokeOpacity = "0.2";  // Lower opacity for others
        }
    });
}
</script>
"""

# URL to the GTFS data
url_b = "https://rrgtfsfeeds.s3.amazonaws.com/gtfs_b.zip"
url_bx = "https://rrgtfsfeeds.s3.amazonaws.com/gtfs_bx.zip"
url_m = "https://rrgtfsfeeds.s3.amazonaws.com/gtfs_m.zip"
url_q = "https://rrgtfsfeeds.s3.amazonaws.com/gtfs_q.zip"
url_si = "https://rrgtfsfeeds.s3.amazonaws.com/gtfs_si.zip"
url_busco = "https://rrgtfsfeeds.s3.amazonaws.com/gtfs_busco.zip"

# Function to download and extract the ZIP file from the URL
@st.cache_data(show_spinner=False)
def fetch_and_extract_gtfs(url):
    # Download the file from the URL
    response = requests.get(url)
    
    # Check if the request was successful (status code 200)
    if response.status_code == 200:
        # Create a BytesIO object from the response content
        zip_file = io.BytesIO(response.content)
        
        # Extract the ZIP file in memory
        with zipfile.ZipFile(zip_file, 'r') as zip_ref:
            # Read 'shapes.txt' into DataFrame
            with zip_ref.open('shapes.txt') as f_shapes:
                df_shapes = pd.read_csv(f_shapes)
            
            # Read 'trips.txt' into DataFrame
            with zip_ref.open('trips.txt') as f_trips:
                df_trips = pd.read_csv(f_trips)
            
            # Return the DataFrames
            return df_shapes, df_trips
    else:
        raise Exception(f"Failed to download file, status code: {response.status_code}")

# Fetch and display stops data
@st.cache_data(show_spinner=False)
def make_gdf(df_shapes, df_trips):
    df_shapes['shape_pt_sequence'] = pd.to_numeric(df_shapes['shape_pt_sequence'])
    # Sort data to ensure points are in correct order
    df_shapes = df_shapes.sort_values(by=['shape_id', 'shape_pt_sequence'])
    # Group by shape_id and create LineString geometry
    lines = df_shapes.groupby('shape_id').apply(
        lambda x: sp.geometry.LineString(x[['shape_pt_lon', 'shape_pt_lat']].values)
    ).reset_index(name='geometry')
    # # Convert to GeoDataFrame
    df_trips = df_trips[['route_id','direction_id','shape_id']]
    df_trips = df_trips.drop_duplicates().reset_index(drop = True)
    gdf = gpd.GeoDataFrame(lines, geometry='geometry', crs="EPSG:4326")  # WGS 84 CRS
    gdf_join = gdf.merge(df_trips, on='shape_id', how='left')
    return gdf_join

@st.cache_data(show_spinner=False)
def load_all_gtfs():
    urls = {
        "Brooklyn": url_b,
        "Bronx": url_bx,
        "Manhattan": url_m,
        "Queens": url_q,
        "Staten Island": url_si
    }
    gdfs = {}
    for borough, url in urls.items():
        df_shapes, df_trips = fetch_and_extract_gtfs(url)
        gdfs[borough] = make_gdf(df_shapes, df_trips)
    
    return gdfs
# Function to fetch bus data
@st.cache_data(show_spinner=False)
def fetch_bus_data(route_id=None, date_start=None, date_end=None, borough="brooklyn", limit=1000):
    # Define API endpoint and base query
    BASE_API = "https://data.ny.gov/resource/58t6-89vi.json?"
    query_speeds = {
        '$select': 'route_id, AVG(average_road_speed) as avg_speed',
        '$group': 'route_id',
        '$limit': limit,
        '$order': 'avg_speed'
    }
    
    # Build WHERE clause based on filters
    where_conditions = []
    
    if route_id:
        where_conditions.append(f'route_id="{route_id}"')
    if borough:
        where_conditions.append(f'borough="{borough}"')
    if date_start:
        where_conditions.append(f'timestamp>="{date_start}T00:00:00"')
    if date_end:
        where_conditions.append(f'timestamp<="{date_end}T23:59:59"')
    
    if where_conditions:
        query_speeds['$where'] = ' AND '.join(where_conditions)
    
    # Fetch data
    url_speeds = BASE_API + urlencode(query_speeds)
    response_speeds = urllib.request.urlopen(url_speeds)
    data_speeds = json.loads(response_speeds.read().decode())
    
    # Convert to DataFrame
    df_speeds = pd.DataFrame(data_speeds)
    return df_speeds

def get_latest_data_date():
    # Socrata Open Data API endpoint for the dataset
    dataset_id = "58t6-89vi"
    base_url = f"https://data.ny.gov/resource/{dataset_id}.json"

    # Query parameters to get the most recent date
    query = {
        "$select": "MAX(timestamp) as latest_date"
    }

    # Make the request to the API
    response = requests.get(base_url, params=query)

    if response.status_code == 200:
        data = response.json()
        if data and 'latest_date' in data[0]:
            # Convert the date string to a datetime object
            latest_date = datetime.strptime(data[0]['latest_date'], '%Y-%m-%dT%H:%M:%S.%f')
            return latest_date
        else:
            raise ValueError("No date information found in the dataset.")
    else:
        raise ConnectionError(f"Failed to fetch data: {response.status_code}")
# Set up the Streamlit page
st.title("NYC Bus Data Explorer")

# Sidebar controls
st.sidebar.header("Filters")

# Date range selector
col1, col2 = st.sidebar.columns(2)


try:
    latest_date = get_latest_data_date()
    with col1:
        date_start = st.date_input("Start Date", max_value = latest_date)
    with col2:
        date_end = st.date_input("End Date", max_value=latest_date)
except Exception as e:
    st.error(f"Error fetching the latest data date: {e}")

# Borough selector
boroughs = ["Manhattan", "Brooklyn", "Queens", "Bronx", "Staten Island"]
borough_filter = st.sidebar.selectbox("Select Borough", boroughs)
gdf_data = load_all_gtfs()
gdf_join = gdf_data[borough_filter]

# Number of results limiter

import json

def render_mapbox_map(gdf_routes):
    mapbox_access_token = "pk.eyJ1Ijoic2NoZXcyIiwiYSI6ImNsOWVjNmd0ZDI3Y2gzcGw5aTVnMnNoMXMifQ.uYA52Qg_9j0JJD8nO7Y64w"

    # Convert route geometries to JSON format
    route_features = []
    for _, row in gdf_routes.iterrows():
        feature = {
            "type": "Feature",
            "properties": {
                "route_id": row["route_id"],
                "avg_speed": row["avg_speed"]
            },
            "geometry": {
                "type": "LineString",
                "coordinates": [[lon, lat] for lon, lat in row.geometry.coords]
            }
        }
        route_features.append(feature)

    geojson_data = {
        "type": "FeatureCollection",
        "features": route_features
    }

    # Read the HTML template hello
    with open("mapbox_template.html", "r") as file:
        html_template = file.read()

    # Replace placeholders with actual data
    html_code = html_template.replace("{mapbox_access_token}", mapbox_access_token)
    html_code = html_code.replace("{geojson_data}", json.dumps(geojson_data))

    return html_code

# Add a button to trigger the data fetch
if st.sidebar.button("Fetch Data",key="fetch_button"):
    try:
        # Fetch the data
        with st.spinner("Fetching and processing data..."):

            df = fetch_bus_data(
                date_start=date_start.strftime('%Y-%m-%d') if date_start else None,
                date_end=date_end.strftime('%Y-%m-%d') if date_end else None,
                borough=borough_filter #,
                # limit=limit
            )
        
        # Display the results
        st.header("Results")
        
        # Convert avg_speed to numeric and round to 2 decimal places
        if 'avg_speed' in df.columns:
            df['avg_speed'] = pd.to_numeric(df['avg_speed']).round(2)

        # Display basic statistics
        if not df.empty:
            st.subheader("Summary Statistics")
            col1, col2, col3 = st.columns(3)
            with col1:
                st.metric("Average Speed", f"{df['avg_speed'].mean():.2f} mph")
            with col2:
                st.metric("Fastest Route", f"Route {df.loc[df['avg_speed'].idxmax(), 'route_id']}")
            with col3:
                st.metric("Slowest Route", f"Route {df.loc[df['avg_speed'].idxmin(), 'route_id']}")

            st.subheader("Map Visualization")
            # st.subheader(os.listdir(os.curdir))


            df['avg_speed'] = pd.to_numeric(df['avg_speed'], errors='coerce').round(2)
            gdf_routes = gdf_join.merge(df, how = "left", on = "route_id").dropna()
            gdf_routes["geometry"] = gdf_routes["geometry"].simplify(0.0001)  # Simplifies geometries for faster rendering
            map_center = gdf_routes.geometry.centroid.unary_union.centroid
            if not gdf_routes.empty:
                st.subheader("Bus Routes Map")
                mapbox_html = render_mapbox_map(gdf_routes)
                components.html(mapbox_html, height=600)
            # Display the full dataset
            st.subheader("Detailed Data")
            st.dataframe(gdf_routes)

            # Download button for the data
            csv = df.to_csv(index=False)
            st.download_button(
                label="Download Data as CSV",
                data=csv,
                file_name="bus_data.csv",
                mime="text/csv"
            )
            
        else:
            st.warning("No data found for the selected filters.")

    except Exception as e:
        st.error(f"An error occurred: {str(e)}")
else:
    st.info("Use the filters in the sidebar and click 'Fetch Data' to load bus data.")


route_id          service_id                           trip_id  \
0         B82+       EN_H5-Weekday    EN_H5-Weekday-028500_SBS82_901   
1         B82+       EN_H5-Weekday    EN_H5-Weekday-034800_SBS82_901   
2         B82+       EN_H5-Weekday    EN_H5-Weekday-039800_SBS82_913   
3         B82+       EN_H5-Weekday    EN_H5-Weekday-047300_SBS82_913   
4         B82+       EN_H5-Weekday    EN_H5-Weekday-029700_SBS82_902   
...        ...                 ...                               ...   
57700       B6  UP_A5-Weekday-SDon  UP_A5-Weekday-SDon-136000_B6_300   
57701       B6  UP_A5-Weekday-SDon  UP_A5-Weekday-SDon-137200_B6_309   
57702       B6  UP_A5-Weekday-SDon  UP_A5-Weekday-SDon-093500_B6_232   
57703       B6  UP_A5-Weekday-SDon  UP_A5-Weekday-SDon-093700_B6_305   
57704       B6  UP_A5-Weekday-SDon  UP_A5-Weekday-SDon-094000_B6_235   

                                  trip_headsign  direction_id  block_id  \
0      SELECT BUS BENSNHRST BAY 38 via FLATLNDS             1  36346047   
1       SELECT BUS SPRING CRK SEAVIEW via KINGS             0  36346047   
2      SELECT BUS BENSNHRST BAY 38 via FLATLNDS             1  36346059   
3       SELECT BUS SPRING CRK SEAVIEW via KINGS             0  36346059   
4      SELECT BUS BENSNHRST BAY 38 via FLATLNDS             1  36346048   
...                                         ...           ...       ...   
57700          BENSONHURST - 25 AV - CROPSEY AV             1  36458175   
57701          BENSONHURST - 25 AV - CROPSEY AV             1  36458163   
57702          BENSONHURST - 25 AV - CROPSEY AV             1  36457749   
57703          BENSONHURST - 25 AV - CROPSEY AV             1  36457690   
57704          BENSONHURST - 25 AV - CROPSEY AV             1  36457684   

        shape_id  
0      SBS821519  
1      SBS821520  
2      SBS821519  
3      SBS821520  
4      SBS821519  
...          ...  
57700    B6O0066  
57701    B6O0066  
57702    B6O0063  
57703    B6O0063  
57704    B6O0063  

[57705 rows x 7 columns]

In [19]:
import shapely as sp
# Convert shape_pt_sequence to numeric to ensure correct ordering
shapes['shape_pt_sequence'] = pd.to_numeric(shapes['shape_pt_sequence'])

# Sort data to ensure points are in correct order
shapes = shapes.sort_values(by=['shape_id', 'shape_pt_sequence'])
shapes
# Group by shape_id and create LineString geometry
lines = shapes.groupby('shape_id').apply(
    lambda x: sp.LineString(x[['shape_pt_lon', 'shape_pt_lat']].values)
).reset_index(name='geometry')

# # Convert to GeoDataFrame
gdf = gpd.GeoDataFrame(lines, geometry='geometry', crs="EPSG:4326")  # WGS 84 CRS
gdf


shape_id                                           geometry
0       B10025  LINESTRING (-73.93976 40.5782, -73.9398 40.578...
1       B10026  LINESTRING (-73.93976 40.5782, -73.9398 40.578...
2       B10052  LINESTRING (-74.02854 40.62189, -74.02869 40.6...
3       B10053  LINESTRING (-73.94002 40.57833, -73.94072 40.5...
4       B10054  LINESTRING (-73.98531 40.59678, -73.98528 40.5...
5       B10055  LINESTRING (-73.96548 40.57674, -73.96509 40.5...
6       B10057  LINESTRING (-73.93976 40.5782, -73.9398 40.578...
7       B10058  LINESTRING (-73.94002 40.57833, -73.94072 40.5...
8      B110014  LINESTRING (-73.94676 40.63196, -73.94769 40.6...
9      B110015  LINESTRING (-73.95269 40.63198, -73.95257 40.6...
10     B110016  LINESTRING (-73.98156 40.63481, -73.98201 40.6...
11     B110047  LINESTRING (-74.00998 40.6449, -74.00867 40.64...
12     B110048  LINESTRING (-74.02313 40.64549, -74.02252 40.6...
13     B120015  LINESTRING (-73.89999 40.67674, -73.90001 40.6...
14     B120019  LINESTRING (-73.96114 40.65516, -73.96007 40.6...
15     B120024  LINESTRING (-73.93962 40.6577, -73.93962 40.65...
16     B130027  LINESTRING (-73.87687 40.65271, -73.87632 40.6...
17     B130032  LINESTRING (-73.91933 40.70436, -73.91923 40.7...
18     B140022  LINESTRING (-73.93123 40.66858, -73.92792 40.6...
19     B140023  LINESTRING (-73.86274 40.66476, -73.86269 40.6...
20     B150027  LINESTRING (-73.86083 40.66922, -73.86054 40.6...
21     B150031  LINESTRING (-73.82465 40.66155, -73.82509 40.6...
22     B150032  LINESTRING (-73.94139 40.69972, -73.9413 40.69...
23     B150033  LINESTRING (-73.94139 40.69972, -73.9413 40.69...
24     B150037  LINESTRING (-73.89259 40.66205, -73.89109 40.6...
25     B160031  LINESTRING (-73.98528 40.64181, -73.98514 40.6...
26     B160066  LINESTRING (-73.9627 40.66055, -73.96278 40.66...
27     B160067  LINESTRING (-74.03521 40.61171, -74.03528 40.6...
28    B16C0009  LINESTRING (-74.03521 40.61171, -74.03528 40.6...
29    B16C0010  LINESTRING (-73.9627 40.66055, -73.96278 40.66...
30    B16O0031  LINESTRING (-74.00568 40.63298, -74.00632 40.6...
31    B16O0034  LINESTRING (-74.03998 40.62792, -74.03993 40.6...
32    B16O0035  LINESTRING (-74.03998 40.62792, -74.03993 40.6...
33    B16O0036  LINESTRING (-74.03718 40.61406, -74.03737 40.6...
34    B16O0037  LINESTRING (-74.00568 40.63298, -74.00632 40.6...
35    B16O0038  LINESTRING (-73.98528 40.64181, -73.98514 40.6...
36    B16O0039  LINESTRING (-73.98528 40.64181, -73.98514 40.6...
37    B16O0041  LINESTRING (-74.03918 40.62523, -74.03912 40.6...
38    B16O0042  LINESTRING (-74.03521 40.61171, -74.03528 40.6...
39    B16O0043  LINESTRING (-74.03718 40.61406, -74.03737 40.6...
40    B16O0044  LINESTRING (-73.9627 40.66055, -73.96278 40.66...
41    B16O0152  LINESTRING (-74.0154 40.62651, -74.01503 40.62...
42     B170092  LINESTRING (-73.93123 40.66858, -73.93114 40.6...
43     B170989  LINESTRING (-73.90063 40.62778, -73.90264 40.6...
44     B170993  LINESTRING (-73.88169 40.63905, -73.8817 40.63...
45     B170994  LINESTRING (-73.93123 40.66858, -73.93114 40.6...
46     B200030  LINESTRING (-73.90335 40.67812, -73.9033 40.67...
47     B200033  LINESTRING (-73.8967 40.7057, -73.89656 40.705...
48     B200034  LINESTRING (-73.86324 40.66483, -73.86321 40.6...
49     B200039  LINESTRING (-73.9022 40.70467, -73.90233 40.70...
50      B20010  LINESTRING (-73.95708 40.60739, -73.9569 40.60...
51     B200114  LINESTRING (-73.86324 40.66483, -73.86321 40.6...
52      B20012  LINESTRING (-73.92194 40.60945, -73.92241 40.6...
53     B240021  LINESTRING (-73.95445 40.73016, -73.95423 40.7...
54     B240022  LINESTRING (-73.95941 40.70956, -73.95921 40.7...
55     B240102  LINESTRING (-73.94324 40.73253, -73.94332 40.7...
56     B250031  LINESTRING (-73.89999 40.67674, -73.90001 40.6...
57     B250075  LINESTRING (-73.99195 40.70261, -73.9918 40.70...
58     B260018  LINESTRING (-73.91044 40.69918, -73.90954 40.6...
59     B260021  LINESTRING (-73.99108 40.69598

In [55]:
trips_c = trips[['route_id','direction_id','shape_id']]
trips_c = trips_c.drop_duplicates().reset_index(drop = True)

In [62]:
gdf_join = gdf.merge(trips_c, on = 'shape_id',how='left')
gdf_join
gdf_join.to_file("gdf_join.geojson", driver="GeoJSON")


In [63]:
gdf_join = gdf.merge(trips_c, on = 'shape_id',how='left')
gdf_join
gdf_join.to_file("gdf_join.geojson", driver="GeoJSON")

test = gpd.read_file("gdf_join.geojson")
test


shape_id route_id  direction_id  \
0       B10025       B1             0   
1       B10026       B1             0   
2       B10052       B1             1   
3       B10053       B1             0   
4       B10054       B1             1   
5       B10055       B1             1   
6       B10057       B1             0   
7       B10058       B1             0   
8      B110014      B11             1   
9      B110015      B11             1   
10     B110016      B11             1   
11     B110047      B11             0   
12     B110048      B11             0   
13     B120015      B12             1   
14     B120019      B12             0   
15     B120024      B12             0   
16     B130027      B13             0   
17     B130032      B13             1   
18     B140022      B14             0   
19     B140023      B14             1   
20     B150027      B15             1   
21     B150031      B15             1   
22     B150032      B15             0   
23     B150033      B15             0   
24     B150037      B15             0   
25     B160031      B16             1   
26     B160066      B16             1   
27     B160067      B16             0   
28    B16C0009      B16             0   
29    B16C0010      B16             1   
30    B16O0031      B16             1   
31    B16O0034      B16             0   
32    B16O0035      B16             0   
33    B16O0036      B16             0   
34    B16O0037      B16             1   
35    B16O0038      B16             1   
36    B16O0039      B16             1   
37    B16O0041      B16             0   
38    B16O0042      B16             0   
39    B16O0043      B16             0   
40    B16O0044      B16             1   
41    B16O0152      B16             0   
42     B170092      B17             1   
43     B170989      B17             0   
44     B170993      B17             0   
45     B170994      B17             1   
46     B200030      B20             1   
47     B200033      B20             1   
48     B200034      B20             0   
49     B200039      B20             1   
50      B20010       B2             0   
51     B200114      B20             0   
52      B20012       B2             1   
53     B240021      B24             1   
54     B240022      B24             0   
55     B240102      B24             0   
56     B250031      B25             1   
57     B250075      B25             0   
58     B260018      B26             1   
59     B260021      B26             0   
60      B30012       B3             1   
61      B30018       B3             0   
62      B30063       B3             1   
63     B310011      B31             0   
64     B310049      B31             1   
65     B310051      B31             1   
66     B320037      B32             0   
67     B320039      B32             1   
68     B320041      B32             1   
69     B350011      B35             0   
70     B350012      B35             0   
71     B350013      B35             0   
72     B350204      B35             1   
73     B350209      B35             1   
74     B350211      B35             1   
75     B350212      B35             1   
76     B360008      B36             0   
77     B360009      B36             0   
78     B360020      B36             1   
79     B360022      B36             1   
80     B370003      B37             0   
81     B370004      B37             1   
82     B380411      B38             0   
83     B380412      B38             0   
84     B380413      B38             0   
85     B380417      B38             1   
86     B380418      B38             1   
87     B380419      B38             1   
88     B390007      B39             0   
89     B390009      B39             1   
90      B40014       B4             1   
91      B40015       B4             1   
92      B40016       B4             0   
93     B410006      B41             1   
94     B410044      B41             1   
95     B410045      B41             1   
96     B410046      B41      

In [68]:
import zipfile
import requests
import io
import pandas as pd

# URL to the GTFS data
url = "https://rrgtfsfeeds.s3.amazonaws.com/gtfs_b.zip"

# Function to download and extract the ZIP file from the URL
def fetch_and_extract_gtfs(url):
    # Download the file from the URL
    response = requests.get(url)
    
    # Check if the request was successful (status code 200)
    if response.status_code == 200:
        # Create a BytesIO object from the response content
        zip_file = io.BytesIO(response.content)
        
        # Extract the ZIP file in memory
        with zipfile.ZipFile(zip_file, 'r') as zip_ref:
            # List all files in the ZIP
            # zip_ref.printdir()

            # Read 'shapes.txt' into DataFrame
            with zip_ref.open('shapes.txt') as f_shapes:
                df_shapes = pd.read_csv(f_shapes)
            
            # Read 'trips.txt' into DataFrame
            with zip_ref.open('trips.txt') as f_trips:
                df_trips = pd.read_csv(f_trips)
            
            # Return the DataFrames
            return df_shapes, df_trips
    else:
        raise Exception(f"Failed to download file, status code: {response.status_code}")

# Using Streamlit to display the GTFS data
# import streamlit as st

# st.title("GTFS Data Explorer")

# Fetch and display stops data
df_shapes, df_trips = fetch_and_extract_gtfs(url)
df_trips

df_shapes['shape_pt_sequence'] = pd.to_numeric(shapes['shape_pt_sequence'])

# Sort data to ensure points are in correct order
df_shapes = df_shapes.sort_values(by=['shape_id', 'shape_pt_sequence'])
# Group by shape_id and create LineString geometry
lines = df_shapes.groupby('shape_id').apply(
    lambda x: sp.LineString(x[['shape_pt_lon', 'shape_pt_lat']].values)
).reset_index(name='geometry')

# # Convert to GeoDataFrame
gdf = gpd.GeoDataFrame(lines, geometry='geometry', crs="EPSG:4326")  # WGS 84 CRS
gdf_join = gdf.merge(trips_c, on = 'shape_id',how='left')
# gdf_join
# gdf_join.to_file("gdf_join.geojson", driver="GeoJSON")

# test = gpd.read_file("gdf_join.geojson")
# test

# Display the first few rows of the stops dataset
# st.write("Stops Data", df_stops.head())

# Optionally, you can add more functionality, such as:
# - Allowing the user to explore other GTFS files
# - Visualizing data on maps or tables
# - Filter and download the data


shape_id                                           geometry route_id  \
0       B10025  LINESTRING (-73.93976 40.5782, -73.9398 40.578...       B1   
1       B10026  LINESTRING (-73.93976 40.5782, -73.9398 40.578...       B1   
2       B10052  LINESTRING (-74.02854 40.62189, -74.02869 40.6...       B1   
3       B10053  LINESTRING (-73.94002 40.57833, -73.94072 40.5...       B1   
4       B10054  LINESTRING (-73.98531 40.59678, -73.98528 40.5...       B1   
5       B10055  LINESTRING (-73.96548 40.57674, -73.96509 40.5...       B1   
6       B10057  LINESTRING (-73.93976 40.5782, -73.9398 40.578...       B1   
7       B10058  LINESTRING (-73.94002 40.57833, -73.94072 40.5...       B1   
8      B110014  LINESTRING (-73.94676 40.63196, -73.94769 40.6...      B11   
9      B110015  LINESTRING (-73.95269 40.63198, -73.95257 40.6...      B11   
10     B110016  LINESTRING (-73.98156 40.63481, -73.98201 40.6...      B11   
11     B110047  LINESTRING (-74.00998 40.6449, -74.00867 40.64...      B11   
12     B110048  LINESTRING (-74.02313 40.64549, -74.02252 40.6...      B11   
13     B120015  LINESTRING (-73.89999 40.67674, -73.90001 40.6...      B12   
14     B120019  LINESTRING (-73.96114 40.65516, -73.96007 40.6...      B12   
15     B120024  LINESTRING (-73.93962 40.6577, -73.93962 40.65...      B12   
16     B130027  LINESTRING (-73.87687 40.65271, -73.87632 40.6...      B13   
17     B130032  LINESTRING (-73.91933 40.70436, -73.91923 40.7...      B13   
18     B140022  LINESTRING (-73.93123 40.66858, -73.92792 40.6...      B14   
19     B140023  LINESTRING (-73.86274 40.66476, -73.86269 40.6...      B14   
20     B150027  LINESTRING (-73.86083 40.66922, -73.86054 40.6...      B15   
21     B150031  LINESTRING (-73.82465 40.66155, -73.82509 40.6...      B15   
22     B150032  LINESTRING (-73.94139 40.69972, -73.9413 40.69...      B15   
23     B150033  LINESTRING (-73.94139 40.69972, -73.9413 40.69...      B15   
24     B150037  LINESTRING (-73.89259 40.66205, -73.89109 40.6...      B15   
25     B160031  LINESTRING (-73.98528 40.64181, -73.98514 40.6...      B16   
26     B160066  LINESTRING (-73.9627 40.66055, -73.96278 40.66...      B16   
27     B160067  LINESTRING (-74.03521 40.61171, -74.03528 40.6...      B16   
28    B16C0009  LINESTRING (-74.03521 40.61171, -74.03528 40.6...      B16   
29    B16C0010  LINESTRING (-73.9627 40.66055, -73.96278 40.66...      B16   
30    B16O0031  LINESTRING (-74.00568 40.63298, -74.00632 40.6...      B16   
31    B16O0034  LINESTRING (-74.03998 40.62792, -74.03993 40.6...      B16   
32    B16O0035  LINESTRING (-74.03998 40.62792, -74.03993 40.6...      B16   
33    B16O0036  LINESTRING (-74.03718 40.61406, -74.03737 40.6...      B16   
34    B16O0037  LINESTRING (-74.00568 40.63298, -74.00632 40.6...      B16   
35    B16O0038  LINESTRING (-73.98528 40.64181, -73.98514 40.6...      B16   
36    B16O0039  LINESTRING (-73.98528 40.64181, -73.98514 40.6...      B16   
37    B16O0041  LINESTRING (-74.03918 40.62523, -74.03912 40.6...      B16   
38    B16O0042  LINESTRING (-74.03521 40.61171, -74.03528 40.6...      B16   
39    B16O0043  LINESTRING (-74.03718 40.61406, -74.03737 40.6...      B16   
40    B16O0044  LINESTRING (-73.9627 40.66055, -73.96278 40.66...      B16   
41    B16O0152  LINESTRING (-74.0154 40.62651, -74.01503 40.62...      B16   
42     B170092  LINESTRING (-73.93123 40.66858, -73.93114 40.6...      B17   
43     B170989  LINESTRING (-73.90063 40.62778, -73.90264 40.6...      B17   
44     B170993  LINESTRING (-73.88169 40.63905, -73.8817 40.63...      B17   
45     B170994  LINESTRING (-73.93123 40.66858, -73.93114 40.6...      B17   
46     B200030  LINESTRING (-73.90335 40.67812, -73.9033 40.67...      B20   
47     B200033  LINESTRING (-73.8967 40.7057, -73.89656 40.705...      B20   
48     B200034  LINESTRING (-73.86324 40.66483, -73.86321 40.6...      B20   
49     B200039  LINESTRING (-73.9022 40.70467, -73.90233 40.70...      B20   
50      B20010  LINESTRING (

In [54]:
#  Calculate map center (mean of all points)
center_lat = gdf_join.geometry.centroid.y.mean()
center_lon = gdf_join.geometry.centroid.x.mean()

# Create a folium map centered at the calculated location
m = folium.Map(location=[center_lat, center_lon], zoom_start=13)

# Generate a unique color for each route_id using a colormap
unique_route_ids = gdf_join['route_id'].unique()
num_routes = len(unique_route_ids)
colors = plt.cm.get_cmap('tab10', num_routes)  # Use a qualitative colormap (e.g., 'tab10')

# Create a color dictionary for each route_id
route_colors = {route_id: f"#{int(colors(i)[0]*255):02X}{int(colors(i)[1]*255):02X}{int(colors(i)[2]*255):02X}" 
                for i, route_id in enumerate(unique_route_ids)}

# Add each route as a line with its assigned color
for _, row in gdf_join.iterrows():
    folium.PolyLine(
        locations=[(lat, lon) for lon, lat in row.geometry.coords],  # Extract coordinates correctly
        color=route_colors[row['route_id']],  # Assign color based on route_id
        weight=3,
        opacity=0.8,
        popup=f"Route ID: {row['route_id']}"
    ).add_to(m)

# Display the map
m